#### Notebook for visualisation of gene programmes from `NicheCompass`
- **Developed by:** Anna Maguza
- **Modified by**: Carlos Talavera-López
- **Faculty of Medicine, University of Würzburg**
- **Creation Date:** 5th of July 2024
- **Last modified**: 241007

### Load required modules

In [33]:
import ast
import mygene
import numpy as np
import scanpy as sc
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from biomart import BiomartServer
from collections import defaultdict

### Set up working environment

In [3]:
sc.settings.verbosity = 3
sc.logging.print_versions()
sc.settings.set_figure_params(dpi = 180, color_map = 'RdPu', dpi_save = 300, vector_friendly = True, format = 'svg')

-----
anndata     0.10.7
scanpy      1.10.1
-----
PIL                 10.0.0
appnope             0.1.3
asttokens           NA
backcall            0.2.0
colorama            0.4.6
comm                0.1.3
cycler              0.10.0
cython_runtime      NA
dateutil            2.8.2
debugpy             1.6.7
decorator           5.1.1
exceptiongroup      1.1.2
executing           1.2.0
h5py                3.9.0
importlib_resources NA
ipykernel           6.25.0
ipywidgets          8.0.7
jedi                0.18.2
joblib              1.3.2
kiwisolver          1.4.4
legacy_api_wrap     NA
llvmlite            0.40.1
matplotlib          3.7.2
mpl_toolkits        NA
natsort             8.4.0
numba               0.57.1
numpy               1.24.4
packaging           23.1
pandas              2.0.3
parso               0.8.3
pexpect             4.8.0
pickleshare         0.7.5
pkg_resources       NA
platformdirs        3.9.1
plotly              5.24.1
prompt_toolkit      3.0.39
psutil              5.9.

In [6]:
fig_dir = '../figures/'

In [ ]:
server = BiomartServer("http://www.ensembl.org/biomart")
mart = server.datasets['hsapiens_gene_ensembl']

### Read in `anndata` object

In [4]:
adata = sc.read_h5ad('../data/xenium_human_breast_cancer_analysis.h5ad')
adata

AnnData object with n_obs × n_vars = 282363 × 313
    obs: 'cell_id', 'x_centroid', 'y_centroid', 'transcript_counts', 'control_probe_counts', 'control_codeword_counts', 'total_counts', 'cell_area', 'nucleus_area', 'replicates', 'n_genes_by_counts', 'log1p_n_genes_by_counts', 'log1p_total_counts', 'pct_counts_in_top_10_genes', 'pct_counts_in_top_20_genes', 'pct_counts_in_top_50_genes', 'pct_counts_in_top_150_genes', 'n_counts', 'n_genes', 'leiden', 'cell_states', 'batch', 'CXCL12_ligand_receptor_GP', 'CD8A_ligand_receptor_GP', 'CD80_ligand_receptor_GP', 'CD8B_ligand_receptor_GP', 'Abca1_ligand_receptor_target_gene_GP', 'Ace2_ligand_receptor_target_gene_GP', 'Adam17_ligand_receptor_target_gene_GP', 'Adam2_ligand_receptor_target_gene_GP', 'Adgrb1_ligand_receptor_target_gene_GP', 'Adm2_ligand_receptor_target_gene_GP', 'Ahsg_ligand_receptor_target_gene_GP', 'Ang_ligand_receptor_target_gene_GP', 'Ang2_ligand_receptor_target_gene_GP', 'Ang4_ligand_receptor_target_gene_GP', 'Ang5_ligand_recep

### Extract genes and gene weights from programme of interest

In [5]:
df = adata.uns['nichecompass_gp_summary']
df.head()

gp_name all_gp_idx gp_active active_gp_idx  \
0             CXCL12_ligand_receptor_GP          0      True             0   
1               CD8A_ligand_receptor_GP          1      True             1   
2               CD80_ligand_receptor_GP          2      True             2   
3               CD8B_ligand_receptor_GP          3      True             3   
4  Abca1_ligand_receptor_target_gene_GP          4      True             4   

  n_source_genes n_non_zero_source_genes n_target_genes  \
0              1                       1              1   
1              1                       1              1   
2              1                       1              1   
3              1                       1              1   
4              0                       0              2   

  n_non_zero_target_genes gp_source_genes    gp_target_genes  \
0                       1      ['CXCL12']         ['AVPR1A']   
1                       1        ['CD8A']           ['PRF1']   
2                       1        ['CD80']           ['CD8B']   
3                       1        ['CD8B']           ['PRF1']   
4                       1              []  ['CAV1', 'CXCR4']   

  gp_source_genes_weights gp_target_genes_weights gp_source_genes_importances  \
0               [-0.0461]                [0.9449]                    [0.0465]   
1               [-0.4468]               [-0.3082]                    [0.5917]   
2               [-0.2762]                [0.8064]                    [0.2551]   
3                 [0.737]                 [0.215]                    [0.7741]   
4                      []          [0.2084, -0.0]                          []   

  gp_target_genes_importances  
0                    [0.9535]  
1                    [0.4083]  
2                    [0.7449]  
3                    [0.2259]  
4                  [1.0, 0.0]

In [29]:
df_gp37 = df[df['gp_name'] == 'Add-on_37_GP']
gp37_genes = df_gp37['gp_source_genes'].values[0]
gp37_genes

"['KRT16', 'KRT14', 'KRT5', 'KRT6B', 'KRT15', 'C5orf46', 'CLCA2', 'KRT23', 'SERPINA3', 'AVPR1A', 'TACSTD2', 'DSP', 'TAC1', 'PIGR', 'MYLK', 'CEACAM6', 'TCF7', 'OPRPN', 'CEACAM8', 'CLDN4', 'AGR3', 'BASP1', 'KIT', 'JUP', 'NOSTRIN', 'CXCR4', 'SEC11C', 'PTRHD1', 'ERN1', 'ABCC11', 'TUBB2B', 'PDGFRA', 'OXTR', 'IL2RA', 'KRT7', 'RAPGEF3', 'MYH11', 'KLF5', 'S100A14', 'CAV1', 'SH3YL1', 'EGFR', 'C15orf48', 'FOXC2', 'FOXP3', 'C6orf132', 'C2orf42', 'GNLY', 'TPD52', 'PDGFRB', 'SCGB2A1', 'CD14', 'EGFL7', 'USP53', 'LYPD3', 'SVIL', 'ANKRD29', 'GLIPR1', 'CX3CR1', 'LGALSL', 'GJB2', 'RUNX1', 'KRT8', 'PPARG', 'TCEAL7', 'RTKN2', 'CDC42EP1', 'POLR2J3', 'MYO5B', 'KLRB1', 'ITGAX', 'PCLAF', 'HMGA1', 'LAG3', 'ANKRD28', 'CD68', 'KARS', 'MZB1', 'KDR', 'AKR1C1', 'TENT5C', 'AQP1', 'AQP3', 'HOXD8', 'SLC25A37', 'THAP2', 'SMAP2', 'ITM2C', 'ELF5', 'LARS', 'DUSP2', 'FSTL3', 'ESR1', 'EIF4EBP1', 'IL7R', 'GPR183', 'MDM2', 'CRISPLD2', 'CCDC80', 'MKI67', 'CD93', 'MMP1', 'HOXD9', 'DMKN', 'ACTG2', 'NPM3', 'CD4', 'C1QC', 'TFAP2A'

In [31]:
genes_list = ast.literal_eval(gp37_genes)
genes = genes_list[:60]
genes

['KRT16',
 'KRT14',
 'KRT5',
 'KRT6B',
 'KRT15',
 'C5orf46',
 'CLCA2',
 'KRT23',
 'SERPINA3',
 'AVPR1A',
 'TACSTD2',
 'DSP',
 'TAC1',
 'PIGR',
 'MYLK',
 'CEACAM6',
 'TCF7',
 'OPRPN',
 'CEACAM8',
 'CLDN4',
 'AGR3',
 'BASP1',
 'KIT',
 'JUP',
 'NOSTRIN',
 'CXCR4',
 'SEC11C',
 'PTRHD1',
 'ERN1',
 'ABCC11',
 'TUBB2B',
 'PDGFRA',
 'OXTR',
 'IL2RA',
 'KRT7',
 'RAPGEF3',
 'MYH11',
 'KLF5',
 'S100A14',
 'CAV1',
 'SH3YL1',
 'EGFR',
 'C15orf48',
 'FOXC2',
 'FOXP3',
 'C6orf132',
 'C2orf42',
 'GNLY',
 'TPD52',
 'PDGFRB',
 'SCGB2A1',
 'CD14',
 'EGFL7',
 'USP53',
 'LYPD3',
 'SVIL',
 'ANKRD29',
 'GLIPR1',
 'CX3CR1',
 'LGALSL']

In [32]:
gp37_weights = df_gp37['gp_source_genes_weights'].values[0]
weights_list = ast.literal_eval(gp37_weights)
weights = weights_list[:60]
weights

[0.0641,
 0.0633,
 0.0628,
 0.0614,
 0.0422,
 0.0367,
 0.0297,
 0.0292,
 0.0276,
 -0.0234,
 0.0206,
 0.0201,
 -0.0198,
 0.0189,
 0.0183,
 0.0174,
 0.0165,
 0.0154,
 0.0138,
 0.0114,
 0.0105,
 -0.0104,
 0.0103,
 0.0102,
 0.0095,
 -0.0087,
 -0.0083,
 -0.0082,
 -0.0081,
 -0.0081,
 0.0078,
 0.0077,
 0.0075,
 -0.0073,
 0.0072,
 -0.0071,
 0.007,
 0.007,
 0.0069,
 0.0067,
 -0.0064,
 0.0062,
 0.0062,
 0.006,
 -0.0056,
 0.0054,
 -0.0054,
 -0.0053,
 0.0052,
 -0.0052,
 0.0051,
 0.0051,
 -0.0051,
 -0.005,
 0.0049,
 0.0048,
 -0.0048,
 0.0046,
 0.0046,
 -0.0046]

### Classify genes into families and superfamilies

In [64]:
response = mart.search({
    'filters': {
        'external_gene_name': genes
    },
    'attributes': [
        'external_gene_name',
        'gene_biotype',
        'interpro_description', 
        'go_id',               # Use GO IDs for pathway information
        'goslim_goa_description'  # Use GO slim descriptions for pathway names
    ]
})

classification = {}
for line in response.iter_lines():
    line = line.decode('utf-8')
    gene_name, gene_biotype, interpro_description, go_id, go_slim_description = line.split('\t')

    if not interpro_description:
        interpro_description = 'Unknown Family'
    if not go_slim_description:
        go_slim_description = 'Unknown Pathway'

    if go_slim_description not in classification:
        classification[go_slim_description] = {}
    if interpro_description not in classification[go_slim_description]:
        classification[go_slim_description][interpro_description] = []
    classification[go_slim_description][interpro_description].append(gene_name)

print(classification)

{'organelle': {'Zinc finger C2H2-type': ['KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'KLF5', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FOXP3', 'FO

In [65]:
classification

{'organelle': {'Zinc finger C2H2-type': ['KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'KLF5',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',
   'FOXP3',


In [55]:
from biomart import BiomartServer

server = BiomartServer("http://www.ensembl.org/biomart")
mart = server.datasets['hsapiens_gene_ensembl']

attributes = mart.attributes

for attribute in attributes:
    print(attribute)

ensembl_gene_id
ensembl_gene_id_version
ensembl_transcript_id
ensembl_transcript_id_version
ensembl_peptide_id
ensembl_peptide_id_version
ensembl_exon_id
description
chromosome_name
start_position
end_position
strand
band
transcript_start
transcript_end
transcription_start_site
transcript_length
transcript_tsl
transcript_gencode_basic
transcript_appris
transcript_is_canonical
transcript_mane_select
transcript_mane_plus_clinical
external_gene_name
external_gene_source
external_transcript_name
external_transcript_source_name
percentage_gene_gc_content
gene_biotype
transcript_biotype
source
transcript_source
version
transcript_version
peptide_version
external_synonym
phenotype_description
source_name
study_external_id
strain_name
strain_gender
p_value
go_id
name_1006
definition_1006
go_linkage_type
namespace_1003
goslim_goa_accession
goslim_goa_description
biogrid
ccds
chembl
dbass3_name
dbass3_id
dbass5_name
dbass5_id
entrezgene_trans_name
embl
arrayexpress
genecards
hgnc_id
hgnc_symbol


In [44]:
classification = {
    'Cytoskeletal Proteins': {
        'Keratin Family': ['KRT16', 'KRT14', 'KRT5', 'KRT6B', 'KRT15', 'KRT23', 'KRT7'],
        'Tubulin Family': ['TUBB2B'],
        'Regulation of Actin': ['RAPGEF3'],
        'Myosins': ['MYH11']
    },
    'Cell Adhesion and Junctions': {
        'Desmosomes and Junctions': ['DSP', 'JUP', 'CLDN4', 'CEACAM6', 'CEACAM8'],
        'Tight Junctions and Adhesion': ['TACSTD2', 'AGR3', 'LYPD3']
    },
    'Signaling Receptors': {
        'Growth Factors': ['KIT', 'PDGFRA', 'PDGFRB', 'EGFR'],
        'Other': ['AVPR1A', 'OXTR', 'IL2RA']
    },
    'Gene Regulation': {
        'Forkhead Box Family': ['FOXC2', 'FOXP3'],
        'Transcription Factors': ['TCF7', 'KLF5'],
        'Open Reading Frames': ['C15orf48', 'C6orf132', 'C2orf42', 'C5orf46']
    },
    'Enzymes and Metabolic Proteins': {
        'Kinases and Phosphatases': ['MYLK', 'ERN1'],
        'Transporters': ['ABCC11'],
        'Peptidases and Hydrolases': ['SEC11C', 'USP53', 'PTRHD1', 'SH3YL1'],
        'Other': ['LGALSL']
    },
    'Immune System Genes': {
        'Chemokine Receptors': ['CXCR4', 'CX3CR1'],
        'Cell Surface Markers': ['CD14', 'GNLY', 'PIGR'],
        'Inflammatory Mediators': ['S100A14', 'EGFL7'],
        'Immune Regulation': ['TAC1']
    },
    'Secreted Proteins': {
        'Secreted Proteins': ['SERPINA3', 'SCGB2A1'],
        'ECM Proteins': ['CAV1']
    },
    'Cell Organization': {
        'Transport Proteins': ['NOSTRIN'],
        'Structural Proteins': ['SVIL', 'ANKRD29', 'GLIPR1']
    }
}

In [45]:
data = []
for category, subcategories in classification.items():
    for subcategory, genes_list in subcategories.items():
        for gene in genes_list:
            weight = weights[genes.index(gene)]
            data.append([category, subcategory, gene, weight])

df = pd.DataFrame(data, columns=['Category', 'Subcategory', 'Gene', 'Gene Weight'])

ValueError: 'KRT16' is not in list

In [46]:
fig = px.sunburst(df, 
                  path=['Category', 'Subcategory', 'Gene'], 
                  color='Gene Weight',
                  color_continuous_scale='RdYlBu_r')

fig.update_layout(coloraxis_colorbar=dict(
    title="Gene Importance Weight",
    tickvals=[min(df['Gene Weight']), max(df['Gene Weight'])],
))

fig.update_layout(
    width=1000,
    height=1000
)

# Set the same label size for all labels
fig.update_traces(
    textinfo="label",
    insidetextfont=dict(size=15)
)

fig.show()

# Save the figure as a high-quality image
fig.write_image(f'{fig_dir}/RdYlBu_r_add_on_37sunburst_plot.png', scale=3)

ValueError: Value of 'path_0' is not the name of a column in 'data_frame'. Expected one of ['Family', 'Genes'] but received: Category

+ Add-on program 86

In [37]:
gp86_genes = df_gp86['gp_source_genes'].values[0]

+ extract first 60 genes

In [38]:
genes_list = ast.literal_eval(gp86_genes)
genes = genes_list[:60]

In [39]:
genes

['MLPH',
 'EPCAM',
 'FOXA1',
 'ELF3',
 'KRT8',
 'KRT7',
 'FASN',
 'ABCC11',
 'MYO5B',
 'SERHL2',
 'TACSTD2',
 'LYPD3',
 'SCD',
 'ANKRD30A',
 'S100A14',
 'GATA3',
 'DSP',
 'AR',
 'C6orf132',
 'TFAP2A',
 'CEACAM8',
 'TRAF4',
 'DMKN',
 'CLDN4',
 'KLF5',
 'PCLAF',
 'ERBB2',
 'CENPF',
 'CCND1',
 'PTGDS',
 'SLC5A6',
 'TOP2A',
 'TPD52',
 'FBLN1',
 'SH3YL1',
 'AGR3',
 'CEACAM6',
 'SQLE',
 'CCDC80',
 'CTTN',
 'JUP',
 'USP53',
 'CCDC6',
 'NARS',
 'RHOH',
 'RTKN2',
 'OCIAD2',
 'STC1',
 'TCIM',
 'HOOK2',
 'ZNF562',
 'CD79A',
 'PDGFRA',
 'SMS',
 'DPT',
 'MEDAG',
 'ZEB2',
 'IL7R',
 'ESR1',
 'MS4A1']

+ Extract gene weights 

In [40]:
gp86_weights = df_gp86['gp_source_genes_weights'].values[0]

In [41]:
weights_list = ast.literal_eval(gp86_weights)
weights = weights_list[:60]

In [42]:
weights

[0.0552,
 0.0545,
 0.0535,
 0.053,
 0.0527,
 0.0525,
 0.0524,
 0.0521,
 0.0499,
 0.0494,
 0.0489,
 0.0483,
 0.0472,
 0.0472,
 0.0454,
 0.0453,
 0.0452,
 0.0452,
 0.043,
 0.0429,
 0.0427,
 0.0396,
 0.0383,
 0.0382,
 0.0369,
 0.0368,
 0.0364,
 0.036,
 0.0345,
 -0.034,
 0.0339,
 0.0335,
 0.033,
 -0.0319,
 0.031,
 0.0301,
 0.03,
 0.0299,
 -0.0298,
 0.0296,
 0.0295,
 0.0293,
 0.0288,
 0.0286,
 0.0282,
 0.0276,
 0.0275,
 0.027,
 0.0268,
 0.0268,
 0.0266,
 -0.0266,
 -0.0263,
 0.0262,
 -0.0257,
 -0.0256,
 -0.0255,
 -0.0255,
 0.0253,
 -0.0252]

In [43]:
classification = {
    'Cytoskeletal Proteins': {
        'Keratin Family': ['KRT8', 'KRT7'],
        'Myosins': ['MYO5B'],
        'Actin-binding': ['CTTN']
    },
    'Cell Adhesion and Junctions': {
        'Cell Adhesion Molecules': ['EPCAM', 'TACSTD2', 'LYPD3', 'CEACAM8', 'CLDN4'],
        'Desmosomes and Junctions': ['DSP', 'JUP'],
        'ECM Proteins': ['DPT', 'FBLN1', 'FBLN1', 'DPT', 'MEDAG', 'STC1']
    },
    'Gene Regulation': {
        'Forkhead Box Family': ['FOXA1'],
        'Transcription Factors': ['ELF3', 'GATA3', 'KLF5', 'TFAP2A', 'ZEB2'],
        'Open Reading Frames': ['C6orf132']
    },
    'Metabolism': {
        'Fatty Acid Synthesis': ['FASN', 'SCD'],
        'Transporters': ['ABCC11', 'SLC5A6'],
        'Other Enzymes': ['USP53', 'SH3YL1', 'SMS', 'SQLE', 'NARS', 'SERHL2']
    },
    'Immune System Genes': {
        'Cytokines': ['IL7R'],
        'Cell Surface Markers': ['CD79A', 'RHOH', 'RTKN2'],
        'Inflammatory Mediators': ['S100A14'],
        'Immune Regulation': ['TRAF4']
    },
    'Signaling': {
        'Growth Factors': ['PDGFRA', 'ERBB2'],
        'Hormones': ['ESR1', 'AR'],
        'TNF': ['TRAF4'],
        'JAK-STAT': ['OCIAD2'],
        'Wnt/β-catenin': ['TCIM']
    },
    'Cell Cycle and Proliferation': {
        'Cell Cycle Regulators': ['CCND1', 'CENPF', 'TOP2A'],
        'Proliferation Markers': ['PCLAF', 'TPD52']
    }
}

# Create the DataFrame
data = []
for category, subcategories in classification.items():
    for subcategory, genes_list in subcategories.items():
        for gene in genes_list:
            weight = weights[genes.index(gene)]
            data.append([category, subcategory, gene, weight])

df = pd.DataFrame(data, columns=['Category', 'Subcategory', 'Gene', 'Gene Weight'])

In [44]:
fig = px.sunburst(df, 
                  path=['Category', 'Subcategory', 'Gene'], 
                  color='Gene Weight',
                  color_continuous_scale='RdYlBu_r')

fig.update_layout(coloraxis_colorbar=dict(
    title="Gene Importance Weight",
    tickvals=[min(df['Gene Weight']), max(df['Gene Weight'])],
))

fig.update_layout(
    width=1000,
    height=1000
)

# Set the same label size for all labels
fig.update_traces(
    textinfo="label",
    insidetextfont=dict(size=15)
)

fig.show()

# Save the figure as a high-quality image
fig.write_image(f'{fig_dir}/RdYlBu_r_add_on_86sunburst_plot.png', scale=3)

In [46]:
import pkg_resources

for dist in pkg_resources.working_set:
    print(f"{dist.project_name}=={dist.version}")

scikit-misc==0.3.1
Babel==2.14.0
Brotli==1.1.0
MarkupSafe==2.1.5
PyQt5==5.15.10
PyQt5-Qt5==5.15.2
PyQt5-sip==12.13.0
PySocks==1.7.1
PyYAML==6.0.1
Send2Trash==1.8.3
anndata==0.10.5.post1
anyio==4.3.0
archspec==0.2.3
argon2-cffi==23.1.0
argon2-cffi-bindings==21.2.0
array-api-compat==1.6
arrow==1.3.0
asttokens==2.4.1
async-lru==2.0.4
attrs==23.2.0
beautifulsoup4==4.12.3
bleach==6.1.0
boltons==24.0.0
cached-property==1.5.2
certifi==2024.6.2
cffi==1.16.0
chardet==5.2.0
charset-normalizer==3.3.2
click==8.1.7
colorama==0.4.6
comm==0.2.2
conda==24.5.0
conda-build==24.5.1
conda-index==0.5.0
conda-libmamba-solver==24.1.0
conda-package-handling==2.3.0
conda-package-streaming==0.10.0
contourpy==1.2.1
cycler==0.12.1
debugpy==1.8.1
decorator==5.1.1
defusedxml==0.7.1
distro==1.9.0
entrypoints==0.4
ete3==3.1.3
exceptiongroup==1.2.0
executing==2.0.1
faiss-gpu==1.7.2
fastjsonschema==2.19.1
filelock==3.15.1
fonttools==4.51.0
fqdn==1.5.1
frozendict==2.4.4
get-annotations==0.1.2
h11==0.14.0
h2==4.1.0
h5py=